# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Italian restaurant** in **Shanghai**, China.

Since there are lots of restaurants in Berlin we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Italian restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Italian restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Nominatim reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Shanghai center will be obtained using **Nominatim geocoding** of well known Shanghai location (Renmin Guangchang)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Shanghai city center.

Let's first find the latitude & longitude of Shanghai city center, using Nominatim.

In [ ]:
# The code was removed by Watson Studio for sharing.

In [ ]:
!pip install shapely
!pip install pyproj
!pip install geopy
!pip install geocoder

     |████████████████████████████████| 6.6 MB 7.8 MB/s 
ERROR: Operation cancelled by user
     |████████████████████████████████| 98 kB 4.2 MB/s 


In [121]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="app_namne")
location = geolocator.geocode("上海人民广场") #在此处输入目标城市，如上海、New York等（全球支持）
address=location.address
Shanghai_center=(location.latitude, location.longitude)
lat=location.latitude
lon=location.longitude
print('Coordinate of {}: {}'.format(address, Shanghai_center))
print(lat)
print(lon)

Coordinate of 人民广场, 西藏中路, 同益里, 南京东路街道, 上海市, 黄浦区, 200001, 中国: (31.23392545, 121.47103760545141)
31.23392545
121.47103760545141


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Alexanderplatz. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [ ]:
import shapely.geometry
 
#!pip install pyproj
import pyproj
 
import math
 
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]
 
def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]
 
def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)
 
print('Coordinate transformation check')
print('-------------------------------')
print('Shanghai center longitude={}, latitude={}'.format(Shanghai_center[1], Shanghai_center[0]))
x, y = lonlat_to_xy(Shanghai_center[1],Shanghai_center[0])
print('Shanghai center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Shanghai center longitude={}, latitude={}'.format(lo, la))
print(Shanghai_center[1])
print(Shanghai_center[0])

Coordinate transformation check
-------------------------------
Shanghai center longitude=121.47103760545141, latitude=31.23392545
Shanghai center UTM X=7873960.231567714, Y=12777134.670694008
Shanghai center longitude=121.4710376054437, latitude=31.23392544999416
121.47103760545141
31.23392545


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [ ]:
Shanghai_center_x, Shanghai_center_y = lonlat_to_xy(Shanghai_center[1], Shanghai_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = Shanghai_center_x -6000
x_step = 600
y_min = Shanghai_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(Shanghai_center_x, Shanghai_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecat

364 candidate neighborhood centers generated.


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [ ]:
!pip install folium

import folium

In [ ]:
len(latitudes)

364

In [165]:
#radius=3540 around Renminguangchang select 364 candidate neighborhood centers.
map_Shanghai = folium.Map(location=Shanghai_center, zoom_start=13)
folium.Marker(Shanghai_center, popup='Renmin Gaungchang').add_to(map_Shanghai)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Shanghai) 
    folium.Circle([lat, lon], radius=170, color='blue', fill=False).add_to(map_Shanghai)
    #folium.Marker([lat, lon]).add_to(map_Shanghai)
map_Shanghai

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Renmin Guangchang. 

Let's now use Nominatim to get approximate addresses of those locations.

In [ ]:
##Try function to return address
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="app_namne")
location = geolocator.reverse(str(Shanghai_center[0])+","+str(Shanghai_center[1]))
address=location.address
print(location.address)

人民广场, 西藏中路, 同益里, 南京东路街道, 上海市, 黄浦区, 200001, 中国


In [167]:
def get_address(latitude, longitude, verbose=False):
    try:
      from geopy.geocoders import Nominatim
      geolocator = Nominatim(user_agent="app_namne")
      location = geolocator.reverse(str(latitude)+","+str(longitude))
      #if verbose:
      print('Nominatim result =>', location)
      address=location.address
      return address
    except:
        return None

addr = get_address(Shanghai_center[0], Shanghai_center[1], verbose=False)
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(Shanghai_center[0], Shanghai_center[1], addr))

Nominatim result => 人民广场, 西藏中路, 同益里, 南京东路街道, 上海市, 黄浦区, 200001, 中国
Reverse geocoding check
-----------------------
Address of [31.23392545, 121.47103760545141] is: 人民广场, 西藏中路, 同益里, 南京东路街道, 上海市, 黄浦区, 200001, 中国


In [168]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon, verbose=False)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', 中国', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses: Nominatim result => 中华新路, 静安区, 上海市, 176-0023, 中国
 .Nominatim result => 中远两湾城, 远景路, 宜川路街道, 普陀区, 上海市, 2000065, 中国
 .Nominatim result => M120, 莫干山路, 普陀区, 上海市, 428, 中国
 .Nominatim result => 71, 澳门路, 普陀区, 200060, 中国
 .Nominatim result => Habibi, 江宁路, 江宁路街道, 普陀区, 428, 中国
 .Nominatim result => 北横通道, 静鼎安邦府邸, 静安区, 200042, 中国
 .Nominatim result => 安远路, 江宁路街道, 静安区, 200060, 中国
 .Nominatim result => foot massage heaven, 芷江西路, 芷江西路街道, 王家宅社区, 静安区, 上海市, 176-0023, 中国
 .Nominatim result => 中华新路, 芷江西路街道, 局东村, 王家宅社区, 静安区, 上海市, 200071, 中国
 .Nominatim result => 上海长途客运总站, 交通路, 天目西路街道, 静安区, 上海市, 176-0023, 中国
 .Nominatim result => 卓悦局, 静安区, 上海市, 428, 中国
 .Nominatim result => 西苏州路, 普陀区, 428, 中国
 .Nominatim result => 北横通道, 静鼎安邦府邸, 静安区, 200042, 中国
 .Nominatim result => 玉佛禅寺, 170, 安远路, 江宁路街道, 静安区, 200060, 中国
 .Nominatim result => Marie's Art Supply Store, 新丰路, 江宁路街道, 静安区, 200060, 中国
 .Nominatim result => Grill and Chill, 常德路, 静安寺街道, 静安区, 2000085, 中国
 .Nominatim result => 静安区业余大学, 昌平路,

In [ ]:
addresses[150:170]

['国际和平妇幼保健院, 华山路, 徐汇区, 上海市, 200030',
 '文定路, 创世纪花园, 徐汇区, 上海市, 200030',
 '徐汇区, 上海市, 200030',
 '同济大学, 1239, 四平路, 杨浦区, 200092',
 '杨浦高级中学, 四平路, 鞍山新村, 杨浦区, 上海市, 200092',
 '密云路, 虹口区, 200092',
 '胡蕴琪艺术教育中心, 96, 四达路, 虹口区, 上海市, 200081',
 '虹口区, 200080',
 '邢家桥南路, 虹口区, 200080',
 '东新民路, 局东村, 王家宅社区, 静安区, 上海市, 200071',
 '塘沽路, 东南门, 局西村, 王家宅社区, 静安区, 200085',
 '南苏州路, 外滩街道, 上海市, 黄浦区, 200085',
 '小楊生煎館, 黄河路, 同益里, 南京东路街道, 上海市, 黄浦区, 200001',
 '337南门, 成都北路, 静安区, 200070',
 '瑞金二路街道, 上海市, 黄浦区, 200003',
 '花园饭店, 淮海中路, 瑞金二路街道, 上海市, 黄浦区, 上海市, 200003',
 '汾阳花园酒店, 45, 复兴中路, 翠湖天地, 上海市, 黄浦区, 上海市, 200031',
 'Hollywod, 岳阳路, 小木桥, 徐汇区, 上海市, 200031',
 '中国银行, 建国西路, 小木桥, 徐汇区, 上海市, 2017',
 '快客, 肇嘉浜路, 小木桥, 徐汇区, 上海市, 2017']

Looking good. Let's now place all this into a Pandas dataframe.

In [ ]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations
#df_locations.shape

Address  ...  Distance from center
0                             中华新路, 静安区, 上海市, 176-0023  ...           5992.495307
1                 中远两湾城, 远景路, 宜川路街道, 普陀区, 上海市, 2000065  ...           5840.376700
2                            M120, 莫干山路, 普陀区, 上海市, 428  ...           5747.173218
3                                 71, 澳门路, 普陀区, 200060  ...           5715.767665
4                         Habibi, 江宁路, 江宁路街道, 普陀区, 428  ...           5747.173218
..                                                 ...  ...                   ...
359                沿江风光带, 小东门街道, 上海市, 黄浦区, 上海市, 200011  ...           5747.173218
360                 中山南路, 小东门街道, 上海市, 黄浦区, 上海市, 200011  ...           5715.767665
361  董家渡圣方济各沙勿略堂, 185, 董家渡路, 小东门街道, 上海市, 黄浦区, 上海市, ...  ...           5747.173218
362                         多稼路, 上海市, 黄浦区, 上海市, 200011  ...           5840.376700
363                南浦大桥, 国货路, 半淞园路街道, 上海市, 黄浦区, 200011  ...           5992.495307

[364 rows x 6 columns]

...and let's now save/persist this data into local file.

In [ ]:
df_locations.to_pickle('./locations.pkl')    

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffee shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

Foursquare credentials are defined in hidden cell bellow.

In [ ]:
# Define Foursquare Credentials and Version
import requests
foursquare_client_id = 'QUDRUP4LNJLIKPKUEAVPELVPN5VHUMQYCUKD3INTW5ELNTQT' # your Foursquare ID
foursquare_client_secret = 'GQM43H3EXOBPAHUU3DKELTDWNVL52UMPMTBRQCXIZRGMB5M4'  # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID:' + foursquare_client_id)
print('CLIENT_SECRET:' + foursquare_client_secret)

Your credentails:
CLIENT_ID:QUDRUP4LNJLIKPKUEAVPELVPN5VHUMQYCUKD3INTW5ELNTQT
CLIENT_SECRET:GQM43H3EXOBPAHUU3DKELTDWNVL52UMPMTBRQCXIZRGMB5M4


In [ ]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):
food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues
italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', 中国', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [ ]:
#latitudes

In [ ]:
import requests
venues_all=[]
for lat, lon in zip(latitudes, longitudes):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        venues_all.append(venues)
print('done.')

done.


In [ ]:
#Test
venues_all

In [ ]:
restaurants = {}
italian_restaurants = {}
location_restaurants = []

print('Obtaining venues around candidate locations:', end='')
for venues in venues_all:
    area_restaurants = []
    for venue in venues:
        venue_id = venue[0]
        venue_name = venue[1]
        venue_categories = venue[2]
        venue_latlon = venue[3]
        venue_address = venue[4]
        venue_distance = venue[5]
        is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
        if is_res:
             x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
             restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
             if venue_distance<=300:
                 area_restaurants.append(restaurant)
             restaurants[venue_id] = restaurant
             if is_italian:
                italian_restaurants[venue_id] = restaurant
    location_restaurants.append(area_restaurants)
    print(' .', end='')
print(' done.')
#restaurants, italian_restaurants, location_restaurants

Obtaining venues around candidate locations:

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyp

 .

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


 . . .

...

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyp

 .

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyp

 . . . done.


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


In [ ]:
    # Let's persists this in local file system
    import pickle
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)

In [ ]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 1116
Total number of Italian restaurants: 68
Percentage of Italian restaurants: 6.09%
Average number of restaurants in neighborhood: 6.538461538461538


In [ ]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4d702a88641254813735d893', '阿拉丁新疆风味餐厅', 31.255328843643372, 121.44563742205509, '上海市, 上海市', 290, False, 7872430.057231611, 12771433.988260077)
('50e22bc2e4b019f64f07f37a', 'Holiday Inn Express Restaurant', 31.254298459225005, 121.44832683150847, 'Zháběi, 上海市, 上海市', 334, False, 7872384.447431404, 12771920.297372734)
('4ffa61bce4b038644cb20494', 'Da Niang Dumpling (大娘水饺)', 31.25408928136452, 121.44837146848153, '中兴路1638号 | 1638 Zhongxin Rd., 上海市, 上海市', 328, False, 7872416.000903373, 12771946.572191697)
('5527c863498e5d11804dff88', '九牛二炉', 31.254150258244554, 121.44504038698314, '上海市, 上海市', 53, False, 7872676.933059199, 12771459.383576192)
('4c905d5fb6d1a143694ac30f', 'Hongzi Chicken (红子鸡)', 31.249316256574097, 121.4402363277745, '188 Aomen Rd, Pǔtuó, 上海市', 319, False, 7873881.349207895, 12771223.055908475)
('4b45cb10f964a520661026e3', 'Wagas (沃歌斯)', 31.24443953867173, 121.43762563408016, '155 Changshou Rd | 长寿路155号 (1/F Paris Printemps | 

In [ ]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('55f7a4eb498e7796e9a5d714', 'SALE & PEPE The KITCHEN & BAR', 31.235553676191067, 121.43841699661554, '常徳路800号1階-A2室800SHOW, 上海市', 111, True, 7876345.581455376, 12772264.497506477)
('5af7e8c8c9f907002c886b5a', 'Funkadeli', 31.23184888027929, 121.43556552974364, '163 Yanping Rd (Wuding Rd), Jing’an, 上海市, 200000', 253, True, 7877201.478361639, 12772203.346264048)
('57780770498e61cc07cb8349', 'Bar Centrale', 31.230856926080268, 121.43632124241537, '135 Yanping Road (Wuding Road), 上海市, 上海市', 328, True, 7877306.880315028, 12772406.71150831)
('56bb2be9498ed541a09f2f1a', "Luccio's", 31.23146631559415, 121.43623515646112, '135 Yanping Road | 延平路135号 (Wuding Road | 武定路), 上海市, 上海市', 212, True, 7877211.316893461, 12772336.477111131)
('534a4ba3498e9deb947ba076', 'Delimuses & Magpie Bar', 31.23663440812756, 121.44491370519272, "363 Kanding Rd (Shaanxi N Rd), Jing'an, 上海市", 238, True, 7875634.3865754325, 12773101.483384512)
('547a9aa7498e52f9d4

In [ ]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: 申宴酒楼
Restaurants around location 102: Cloud South (云海肴)
Restaurants around location 103: alma by DN, Wagas (沃歌斯), Sense 8 (誉八仙酒楼), Cloud South (云海肴)
Restaurants around location 104: Little Sheep Hot Pot (小肥羊)
Restaurants around location 105: 
Restaurants around location 106: 富春小笼, 倍乐创意韩国料理
Restaurants around location 107: Zhen Ding Chicken (振鼎鸡), Cha's Restaurant (查餐厅), Dong Lai Shun (东来顺饭庄), Wang Jia Sha (王家沙), Tairyo Teppanyaki (大渔铁板烧), Lapis Yun (藏珑云海), Belloco (倍乐创意韩国料理), Lapis Thai Kitchen
Restaurants around location 108: Little Catch, Café Gray Deluxe, Zhen Ding Chicken (振鼎鸡), Wang Jia Sha (王家沙), Let's Taipei (非常台北), Currify & Taoker, Tairyo Teppanyaki (大渔铁板烧), Kemi (磕米)
Restaurants around location 109: Little Catch, 帥鍋, Kemi (磕米), Currify & Taoker, Heat, 和幸, Jujube Tree (Vegetarian Life Style) (枣子树), Sumo (相扑烧肉)
Restaurants around location 110: 帥鍋, Nongtang Small Wonton (弄堂小馄饨), Muang Thai K

Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [ ]:
map_Shanghai= folium.Map(location=Shanghai_center, zoom_start=13)
folium.Marker(Shanghai_center, popup='RenminGuangchang').add_to(map_Shanghai)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_Shanghai)
map_Shanghai

Looking good. So now we have all the restaurants in area within few kilometers from RenminGuangchang, and we know which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Shanghai that have low restaurant density, particularly those with low number of Italian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Shanghai center** (RenminGuangchang). We have also **identified Italian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Shanghai - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Italian restaurants in radius of 800 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [ ]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 6.538461538461538


Address  ...  Restaurants in area
0                           中华新路, 静安区, 上海市, 176-0023  ...                    1
1               中远两湾城, 远景路, 宜川路街道, 普陀区, 上海市, 2000065  ...                    2
2                          M120, 莫干山路, 普陀区, 上海市, 428  ...                    0
3                               71, 澳门路, 普陀区, 200060  ...                    0
4                       Habibi, 江宁路, 江宁路街道, 普陀区, 428  ...                    4
5                          北横通道, 静鼎安邦府邸, 静安区, 200042  ...                    9
6                            安远路, 江宁路街道, 静安区, 200060  ...                    5
7  foot massage heaven, 芷江西路, 芷江西路街道, 王家宅社区, 静安区,...  ...                    2
8         中华新路, 芷江西路街道, 局东村, 王家宅社区, 静安区, 上海市, 200071  ...                    0
9          上海长途客运总站, 交通路, 天目西路街道, 静安区, 上海市, 176-0023  ...                    3

[10 rows x 7 columns]

OK, now let's calculate the **distance to nearest Italian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [ ]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_locations['Distance to Italian restaurant'] = distances_to_italian_restaurant

In [ ]:
df_locations.head(10)

Address  ...  Distance to Italian restaurant
0                           中华新路, 静安区, 上海市, 176-0023  ...                     2534.614895
1               中远两湾城, 远景路, 宜川路街道, 普陀区, 上海市, 2000065  ...                     2218.548898
2                          M120, 莫干山路, 普陀区, 上海市, 428  ...                     2034.611942
3                               71, 澳门路, 普陀区, 200060  ...                     2019.240526
4                       Habibi, 江宁路, 江宁路街道, 普陀区, 428  ...                     1975.475700
5                          北横通道, 静鼎安邦府邸, 静安区, 200042  ...                     1456.050953
6                            安远路, 江宁路街道, 静安区, 200060  ...                     1028.428175
7  foot massage heaven, 芷江西路, 芷江西路街道, 王家宅社区, 静安区,...  ...                     2866.214037
8         中华新路, 芷江西路街道, 局东村, 王家宅社区, 静安区, 上海市, 200071  ...                     2373.366691
9        上海长途客运总站, 孔家木桥路, 天目西路街道, 静安区, 上海市, 176-0023  ...                     1941.791954

[10 rows x 8 columns]

In [ ]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 949.8471154318443


OK, so **on average Italian restaurant can be found within ~950m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of Shanghai boroughs** on our map and a few circles indicating distance of 1km, 2km and 3km from RenminGuangchang.

In [ ]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

In [ ]:
from folium import plugins
from folium.plugins import HeatMap

map_Shanghai = folium.Map(location=Shanghai_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_Shanghai) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_Shanghai)
folium.Marker(Shanghai_center).add_to(map_Shanghai)
folium.Circle(Shanghai_center, radius=1000, fill=False, color='white').add_to(map_Shanghai)
folium.Circle(Shanghai_center, radius=2000, fill=False, color='white').add_to(map_Shanghai)
folium.Circle(Shanghai_center, radius=3000, fill=False, color='white').add_to(map_Shanghai)
#folium.GeoJson(Shanghai_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Shanghai)
map_Shanghai


Looks like a few pockets of low restaurant density closest to city center can be found ** south-east and north from RenminGuangchang**. 

Let's create another heatmap map showing **heatmap/density of Italian restaurants** only.

In [ ]:
map_Shanghai = folium.Map(location=Shanghai_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_Shanghai) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_Shanghai)
folium.Marker(Shanghai_center).add_to(map_Shanghai)
folium.Circle(Shanghai_center, radius=1000, fill=False, color='white').add_to(map_Shanghai)
folium.Circle(Shanghai_center, radius=2000, fill=False, color='white').add_to(map_Shanghai)
folium.Circle(Shanghai_center, radius=3000, fill=False, color='white').add_to(map_Shanghai)
#folium.GeoJson(Shanghai_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Shanghai)
map_Shanghai

This map is not so 'hot' (Italian restaurants represent a subset of ~6.4% of all restaurants in Shanghai) but it also indicates higher density of existing Italian restaurants directly east and south-west from RenminGuangchang, with closest pockets of **low Italian restaurant density positioned south-east, north-west and north from city center**.

Based on this we will now focus our analysis on areas *south-east, north-west and north from Shaihai center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.0km**. This places our location candidates mostly in boroughs **Jingan and Huangpu** .

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of Huangpu and Jingan closest to Renmin Guangchang.

In [ ]:
roi_width = 4000
roi_height = 4000
roi_center_x = Shanghai_center_x + 1500
roi_center_y = Shanghai_center_y + 2800

roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)

roi_center = [roi_center_lat, roi_center_lon]

map_Shanghai = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_Shanghai)
folium.Marker(Shanghai_center).add_to(map_Shanghai)
folium.Circle(roi_center, radius=2000, color='white', fill=True, fill_opacity=0.4).add_to(map_Shanghai)
#folium.GeoJson(Shanghai_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Shanghai)
map_Shanghai

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Not bad - this nicely covers all the pockets of low restaurant density in Jingan and Huangpu closest to Shanghai center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [ ]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2000
roi_x_min = roi_center_x - 2000

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(41/k)):
    y = roi_y_min + i * y_step
    x_offset = 40 if i%2==0 else 0
    for j in range(0, 41):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2001):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant**.

In [128]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    roi_italian_distances.append(distance)
print('done.')

Generating data on location candidates... done.


In [133]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Italian restaurant':roi_italian_distances})

df_roi_locations.head(10)
#df_roi_locations.shape

Latitude   Longitude  ...  Restaurants nearby  Distance to Italian restaurant
0  31.225396  121.470969  ...                   9                      528.584709
1  31.224946  121.470673  ...                  17                      428.706432
2  31.227160  121.472727  ...                   7                      693.051080
3  31.226709  121.472431  ...                   5                      782.645086
4  31.226258  121.472135  ...                   4                      775.911649
5  31.225807  121.471838  ...                   5                      677.071856
6  31.225356  121.471542  ...                   8                      578.630891
7  31.224905  121.471246  ...                   6                      480.833774
8  31.224455  121.470950  ...                   4                      384.172524
9  31.224004  121.470653  ...                  11                      289.786023

[10 rows x 6 columns]

OK. Let us now **filter** those locations: we're interested only in **locations with no more than 2 restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 800 meters**.

In [162]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Italian restaurant']>=800)
print('Locations with no Italian restaurants within 800m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than two restaurants nearby: 1205
Locations with no Italian restaurants within 800m: 698
Locations with both conditions met: 646


Let's see how this looks on a map.

In [137]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_Shanghai = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_Shanghai)
HeatMap(restaurant_latlons).add_to(map_Shanghai)
folium.Circle(roi_center, radius=2000, color='white', fill=True, fill_opacity=0.6).add_to(map_Shanghai)
folium.Marker(Shanghai_center).add_to(map_Shanghai)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Shanghai) 
#folium.GeoJson(Shanghai_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Shanghai)
map_Shanghai

Looking good. We now have a bunch of locations fairly close to Renmin Guangchang (mostly in Huanpu and Jingan), and we know that each of those locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 800m. Any of those locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [139]:
map_Shanghai = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_Shanghai)
folium.Marker(Shanghai_center).add_to(map_Shanghai)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Shanghai)
#folium.GeoJson(Shanghai_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Shanghai)
map_Shanghai

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and no Italian restaurants at all nearby.

Let us now cluster those locations to create centers of zones containing good locations. Those zones, their centers and addresses will be the final result of our analysis.

In [142]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_Shanghai = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_Shanghai)
HeatMap(restaurant_latlons).add_to(map_Shanghai)
folium.Circle(roi_center, radius=2000, color='white', fill=True, fill_opacity=0.4).add_to(map_Shanghai)
folium.Marker(Shanghai_center).add_to(map_Shanghai)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=200, color='green', fill=True, fill_opacity=0.25).add_to(map_Shanghai) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Shanghai)
#folium.GeoJson(Shanghai_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Shanghai)
map_Shanghai

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.h

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [144]:
from sklearn.cluster import KMeans

map_Shanghai = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(Shanghai_center).add_to(map_Shanghai)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=150, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_Shanghai)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Shanghai)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=200, color='green', fill=False).add_to(map_Shanghai) 
#folium.GeoJson(Shanghai_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Shanghai)
map_Shanghai

Finaly, let's reverse geocode those candidate area centers to get the addresses which can be presented to stakeholders.

In [149]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(lat, lon, verbose=False).replace(', 中国', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, Shanghai_center_x, Shanghai_center_y)
    print('{}{} => {:.1f}km from Renmin Guangchang'.format(addr, ' '*(50-len(addr)), d/1000))

Addresses of centers of areas recommended for further analysis

Google Maps API JSON result => 上海市中华路电话局-办公楼/机房, 734, 中华路, 豫园街道, 上海市, 黄浦区, 上海市, 200021, 中国


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


上海市中华路电话局-办公楼/机房, 734, 中华路, 豫园街道, 上海市, 黄浦区, 上海市, 200021 => 4.7km from Renmin Guangchang
Google Maps API JSON result => 清莲路, 豫园街道, 上海市, 黄浦区, 200021, 中国
清莲路, 豫园街道, 上海市, 黄浦区, 200021                        => 2.3km from Renmin Guangchang


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Google Maps API JSON result => 顺昌路, 卢家湾, 打浦桥街道, 上海市, 黄浦区, 上海市, 200021, 中国
顺昌路, 卢家湾, 打浦桥街道, 上海市, 黄浦区, 上海市, 200021             => 3.4km from Renmin Guangchang


...

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


6, 中华路, 豫园街道, 上海市, 黄浦区, 上海市, 200021                => 2.8km from Renmin Guangchang
Google Maps API JSON result => 李惠利中学, 肇周路, 打浦桥街道, 上海市, 黄浦区, 上海市, 200021, 中国


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


李惠利中学, 肇周路, 打浦桥街道, 上海市, 黄浦区, 上海市, 200021           => 3.8km from Renmin Guangchang
Google Maps API JSON result => 昼锦路, 豫园街道, 上海市, 黄浦区, 200010, 中国
昼锦路, 豫园街道, 上海市, 黄浦区, 200010                        => 2.8km from Renmin Guangchang


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 4km from Alexanderplazt, and about half of those less than 2km from Renmin Guangchang). Although zones are shown on map with a radius of ~200 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in Huangpu boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [157]:
map_Shanghai = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(Shanghai_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_Shanghai)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_Shanghai) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.02).add_to(map_Shanghai)
map_Shanghai

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Berlin (~1116 in our initial area of interest which was 12x12km around Renmin Guangchang), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected north and west from Alexanderplatz, so we focused our attention to areas south-east and east, corresponding to boroughs Huangpu and Jingan which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 4x4km south-east from Renmin Guangchang) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 800m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Berlin center but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Shanghai areas close to center with low number of restaurants (particularly Italian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (Huangpu and Jingan), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or Huangpu River), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.